In [ ]:
import cv2
import mediapipe as mp
import plotly.graph_objects as go
import numpy as np

mp_hands = mp.solutions.hands
cap = cv2.VideoCapture("video3.mp4")

In [ ]:
landmark_frames = []

with mp_hands.Hands(static_image_mode=False, max_num_hands=1) as hands:
    while cap.isOpened():
        ret, frame = cap.read()
        if not ret:
            break

        image_rgb = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
        results = hands.process(image_rgb)

        if results.multi_hand_landmarks:
            hand_landmarks = results.multi_hand_landmarks[0]
            landmark_frames.append([
                (lm.x, lm.y, lm.z)
                for lm in hand_landmarks.landmark
            ])

cap.release()

# Conexiones correctas entre los landmarks (según la documentación de MediaPipe Hands)
connections = [
    # Pulgar
    (0, 1), (1, 2), (2, 3), (3, 4),
    # Índice
    (0, 5), (5, 6), (6, 7), (7, 8),
    # Medio
    (0, 9), (9, 10), (10, 11), (11, 12),
    # Anular
    (0, 13), (13, 14), (14, 15), (15, 16),
    # Meñique
    (0, 17), (17, 18), (18, 19), (19, 20),
    # Conexiones adicionales para formar la palma
    (5, 9), (9, 13), (13, 17)
]

all_landmarks = np.array([pt for frame in landmark_frames for pt in frame])
x_min, x_max = float(all_landmarks[:, 0].min()), float(all_landmarks[:, 0].max())
y_min, y_max = float(all_landmarks[:, 1].min()), float(all_landmarks[:, 1].max())
z_min, z_max = float(all_landmarks[:, 2].min()), float(all_landmarks[:, 2].max())

margin = 0.1
x_range = [x_min - margin, x_max + margin]
y_range = [y_min - margin, y_max + margin]
z_range = [z_min - margin, z_max + margin]

# Ejes de referencia
axes = [
    go.Scatter3d(x=[x_range[0], x_range[1]], y=[y_range[0], y_range[0]], z=[z_range[0], z_range[0]],
                 mode='lines', line=dict(color='red', width=4), name='X'),
    go.Scatter3d(x=[x_range[0], x_range[0]], y=[y_range[0], y_range[1]], z=[z_range[0], z_range[0]],
                 mode='lines', line=dict(color='green', width=4), name='Y'),
    go.Scatter3d(x=[x_range[0], x_range[0]], y=[y_range[0], y_range[0]], z=[z_range[0], z_range[1]],
                 mode='lines', line=dict(color='blue', width=4), name='Z')
]

# Rejilla en z=z_min
floor_lines = []
x_vals = np.linspace(*x_range, 10)
y_vals = np.linspace(*y_range, 10)
for x in x_vals:
    floor_lines.append(go.Scatter3d(x=[x, x], y=y_range, z=[z_min, z_min],
                                    mode='lines', line=dict(color='lightgray', width=1), showlegend=False))
for y in y_vals:
    floor_lines.append(go.Scatter3d(x=x_range, y=[y, y], z=[z_min, z_min],
                                    mode='lines', line=dict(color='lightgray', width=1), showlegend=False))

frames = []
for step, landmarks in enumerate(landmark_frames):
    x, y, z = zip(*landmarks)
    
    # Crear los puntos (scatter)
    scatter = go.Scatter3d(x=x, y=y, z=z, mode='markers',
                          marker=dict(size=5, color='blue'), showlegend=False)
    
    # Crear las líneas de conexión
    line_traces = []
    for connection in connections:
        start_idx, end_idx = connection
        line_trace = go.Scatter3d(
            x=[x[start_idx], x[end_idx]],
            y=[y[start_idx], y[end_idx]],
            z=[z[start_idx], z[end_idx]],
            mode='lines',
            line=dict(color='blue', width=3),
            showlegend=False
        )
        line_traces.append(line_trace)
    
    # Asegurarse de que todos los elementos son listas antes de concatenar
    frame_data = [scatter] + line_traces + axes + floor_lines
    frames.append(go.Frame(data=frame_data, name=str(step)))

# Configuración inicial de la figura
initial_data = [frames[0].data[0]] + [*frames[0].data[1:1+len(connections)]] + axes + floor_lines

fig = go.Figure(
    data=initial_data,
    frames=frames,
    layout=go.Layout(
        updatemenus=[dict(type='buttons', showactive=False,
                          buttons=[dict(label='Play', method='animate',
                                        args=[None, {"frame": {"duration": 50, "redraw": True},
                                                     "fromcurrent": True}])])]
    )
)

fig.update_layout(
    scene=dict(
        aspectmode='cube',
        xaxis=dict(range=x_range, autorange=False),
        yaxis=dict(range=y_range, autorange=False),
        zaxis=dict(range=z_range, autorange=False),
        camera=dict(
            up=dict(x=0, y=1, z=0),
            center=dict(x=0, y=0, z=0),
            eye=dict(x=1.5, y=1.5, z=1.5)
        )
    ),
)

fig.show()

I0000 00:00:1748696309.351001   14401 gl_context_egl.cc:85] Successfully initialized EGL. Major : 1 Minor: 5
I0000 00:00:1748696309.439763   15860 gl_context.cc:369] GL version: 3.2 (OpenGL ES 3.2 NVIDIA 570.144), renderer: NVIDIA GeForce GTX 1660/PCIe/SSE2
W0000 00:00:1748696309.463442   15851 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
W0000 00:00:1748696309.481975   15849 inference_feedback_manager.cc:114] Feedback manager requires a model with a single signature inference. Disabling support for feedback tensors.
